In [80]:
import pickle
import pandas as pd
import folium
import geopy
import geopandas
from tqdm import tqdm
import os
import warnings
warnings.filterwarnings("ignore")
import re
import numpy as np
pd.options.display.max_columns = None
pd.options.mode.chained_assignment = None  # default='warn'

In [2]:
from geopy import Nominatim
locator = Nominatim(user_agent="myGeocoder")
location = locator.geocode("Champ de Mars, Paris, France")

In [3]:
from geopy import ArcGIS
locator = ArcGIS(user_agent="myGeocoder")

# import data
I need to drop the `name` column cause there are some names missing.

In [4]:
os.chdir('..')
os.chdir('data')
os.chdir('pickle')
os.getcwd()

'e:\\Cursos\\00ironhack_DA\\00LABS\\vuelve-conmigo-a-italia\\data\\pickle'

In [5]:
path = os.getcwd()
files = os.listdir(path)
files = [f for f in files if f[-6:] == 'pickle']
files

['dict_booking_0.pickle',
 'dict_booking_1.pickle',
 'dict_booking_2.pickle',
 'dict_booking_3.pickle',
 'dict_booking_4.pickle',
 'dict_booking_5.pickle']

In [6]:
list_dicts = []
for file in files:
    with open(f'{file}', 'rb') as dict_booking:
        dict_booking = pickle.load(dict_booking)
        if len(dict_booking['url']) != len(dict_booking['name']):
            del dict_booking['url'][-1]
        print(len(dict_booking['url']), len(dict_booking['name']), len(dict_booking['pagina']), len(dict_booking['currentPrice']), len(dict_booking['address']))
        list_dicts.append(pd.DataFrame(dict_booking))

2386 2386 2386 2386 2386
1905 1905 1905 1905 1905
1172 1172 1172 1172 1172
1810 1810 1810 1810 1810
807 807 807 807 807
51 51 51 51 51


In [7]:
df_booking = pd.concat(list_dicts).reset_index(drop=True)
df_booking.head(1)

url              name  \
0  https://www.booking.com/hotel/it/b-amp-b-donna...  B&B Donna Teresa   

                                              pagina  \
0  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   

                                             address currentPrice  \
0  [via giuseppe garibaldi, 137/b, 92100 , 92100 ...         € 76   

  previousPrice rating reviewNumber checkingDate  \
0         € 124    9.2  525 reviews   2023-09-03   

                                               image  
0  https://cf.bstatic.com/xdata/images/hotel/squa...

In [8]:
df_booking = df_booking.explode('address')
df_booking.head(1)

url              name  \
0  https://www.booking.com/hotel/it/b-amp-b-donna...  B&B Donna Teresa   

                                              pagina  \
0  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   

                                             address currentPrice  \
0  via giuseppe garibaldi, 137/b, 92100 , 92100 a...         € 76   

  previousPrice rating reviewNumber checkingDate  \
0         € 124    9.2  525 reviews   2023-09-03   

                                               image  
0  https://cf.bstatic.com/xdata/images/hotel/squa...

cleaning duplicated prices 

In [9]:
df_booking['currentPrice'].value_counts()

€ 90          157
€ 85          148
€ 100         142
€ 82          136
€ 80          134
             ... 
€ 112€ 106      1
€ 96€ 92        1
€ 200€ 195      1
€ 93€ 88        1
€ 493           1
Name: currentPrice, Length: 670, dtype: int64

In [10]:
def countEuro(column):
    if column.count('€') == 1:
        return 1
    elif column.count('€') == 2:
        return 2
    else:
        return 0

In [11]:
df_booking['cleanPrice'] = df_booking['currentPrice'].apply(countEuro)

In [12]:
df_booking['cleanPrice'].value_counts()

1    7998
2    1052
Name: cleanPrice, dtype: int64

In [13]:
df_booking_limpio = df_booking[df_booking['cleanPrice'] == 1]
df_booking_sucio = df_booking[df_booking['cleanPrice'] == 2]

In [14]:
df_booking_sucio.head(1)

url  \
6  https://www.booking.com/hotel/it/torre-don-vir...   

                               name  \
6  Torre Don Virgilio Country Hotel   

                                              pagina  \
6  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   

                                             address currentPrice  \
6   via rocciola scrofani, 260, 97015 cannizzara,...   € 168€ 135   

  previousPrice rating reviewNumber checkingDate  \
6           NaN    9.3  383 reviews   2023-09-03   

                                               image  cleanPrice  
6  https://cf.bstatic.com/xdata/images/hotel/squa...           2

In [15]:
df_booking_sucio[[0,1,2]] = df_booking_sucio['currentPrice'].str.split('€', expand=True, n = 2)
df_booking_sucio.head(1)

url  \
6  https://www.booking.com/hotel/it/torre-don-vir...   

                               name  \
6  Torre Don Virgilio Country Hotel   

                                              pagina  \
6  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   

                                             address currentPrice  \
6   via rocciola scrofani, 260, 97015 cannizzara,...   € 168€ 135   

  previousPrice rating reviewNumber checkingDate  \
6           NaN    9.3  383 reviews   2023-09-03   

                                               image  cleanPrice 0     1     2  
6  https://cf.bstatic.com/xdata/images/hotel/squa...           2     168   135

In [16]:
df_booking_sucio['currentPrice'] = '€ ' + df_booking_sucio[2] 
df_booking_sucio['previousPrice'] = '€ ' + df_booking_sucio[1]

In [17]:
df_booking_sucio.drop(['cleanPrice', 0, 1, 2], axis = 1, inplace=True)
df_booking_limpio.drop(['cleanPrice'], axis = 1, inplace=True)
df_booking_sucio.head(1)

url  \
6  https://www.booking.com/hotel/it/torre-don-vir...   

                               name  \
6  Torre Don Virgilio Country Hotel   

                                              pagina  \
6  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   

                                             address currentPrice  \
6   via rocciola scrofani, 260, 97015 cannizzara,...       €  135   

  previousPrice rating reviewNumber checkingDate  \
6        €  168    9.3  383 reviews   2023-09-03   

                                               image  
6  https://cf.bstatic.com/xdata/images/hotel/squa...

In [18]:
df_booking = pd.concat([df_booking_limpio, df_booking_sucio])
print(df_booking.shape)
df_booking.head(1)

(9050, 10)


url              name  \
0  https://www.booking.com/hotel/it/b-amp-b-donna...  B&B Donna Teresa   

                                              pagina  \
0  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   

                                             address currentPrice  \
0  via giuseppe garibaldi, 137/b, 92100 , 92100 a...         € 76   

  previousPrice rating reviewNumber checkingDate  \
0         € 124    9.2  525 reviews   2023-09-03   

                                               image  
0  https://cf.bstatic.com/xdata/images/hotel/squa...

cleaning info -- parkings and other amenities
- comida
- ensuite bathroom
- piscina
- air conditioning

In [19]:
#parking
df_booking['parking'] = df_booking['pagina'].str.lower().str.findall(r'(free parking)')
df_booking = df_booking.explode('parking').drop_duplicates()
df_booking['parking'].value_counts()

free parking    3957
Name: parking, dtype: int64

In [20]:
#air conditioning
df_booking['air_conditioning'] = df_booking['pagina'].str.lower().str.findall(r'(air conditioning)')
df_booking = df_booking.explode('air_conditioning').drop_duplicates()
df_booking['air_conditioning'].value_counts()

air conditioning    6720
Name: air_conditioning, dtype: int64

In [21]:
#private bathroom
df_booking['bathroom'] = df_booking['pagina'].str.lower().str.findall(r'(private bathroom)')
df_booking = df_booking.explode('bathroom').drop_duplicates()
df_booking['bathroom'].value_counts()

private bathroom    6635
Name: bathroom, dtype: int64

In [22]:
#free wifi
df_booking['wifi'] = df_booking['pagina'].str.lower().str.findall(r'(free wifi)')
df_booking = df_booking.explode('wifi').drop_duplicates()
df_booking['wifi'].value_counts()

free wifi    6711
Name: wifi, dtype: int64

In [23]:
#breakfast
df_booking['breakfast'] = df_booking['pagina'].str.lower().str.findall(r'(breakfast)')
df_booking = df_booking.explode('breakfast').drop_duplicates()
df_booking['breakfast'].value_counts()

breakfast    6086
Name: breakfast, dtype: int64

In [24]:
#coffee machine
df_booking['coffee_tea_maker'] = df_booking['pagina'].str.lower().str.findall(r'(tea/coffee maker)')
df_booking = df_booking.explode('coffee_tea_maker').drop_duplicates()
df_booking['coffee_tea_maker'].value_counts()

tea/coffee maker    2702
Name: coffee_tea_maker, dtype: int64

In [25]:
#laundry
df_booking['laundry'] = df_booking['pagina'].str.lower().str.findall(r'(laundry)')
df_booking = df_booking.explode('laundry').drop_duplicates()
df_booking['laundry'].value_counts()

laundry    3675
Name: laundry, dtype: int64

In [26]:
df_booking.head(1)

url              name  \
0  https://www.booking.com/hotel/it/b-amp-b-donna...  B&B Donna Teresa   

                                              pagina  \
0  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   

                                             address currentPrice  \
0  via giuseppe garibaldi, 137/b, 92100 , 92100 a...         € 76   

  previousPrice rating reviewNumber checkingDate  \
0         € 124    9.2  525 reviews   2023-09-03   

                                               image       parking  \
0  https://cf.bstatic.com/xdata/images/hotel/squa...  free parking   

   air_conditioning          bathroom       wifi  breakfast  coffee_tea_maker  \
0  air conditioning  private bathroom  free wifi  breakfast  tea/coffee maker   

   laundry  
0  laundry

In [27]:
print(df_booking.shape)
df_booking.drop_duplicates(inplace=True)
print(df_booking.shape)

(6845, 17)
(6845, 17)


checking dtypes

In [28]:
df_booking.dtypes

url                 object
name                object
pagina              object
address             object
currentPrice        object
previousPrice       object
rating              object
reviewNumber        object
checkingDate        object
image               object
parking             object
air_conditioning    object
bathroom            object
wifi                object
breakfast           object
coffee_tea_maker    object
laundry             object
dtype: object

In [29]:
type(df_booking['address'][0])

str

# Geocoding

In [30]:
from geopy.extra.rate_limiter import RateLimiter
tqdm.pandas()

# 1 - conveneint function to delay between geocoding calls
geocode = RateLimiter(locator.geocode, min_delay_seconds=1)
# 2- - create location column
df_booking['location'] = df_booking['address'].progress_apply(geocode)
# 3 - create longitude, laatitude and altitude from location column (returns tuple)
df_booking['point'] = df_booking['location'].progress_apply(lambda loc: tuple(loc.point) if loc else None)
# 4 - split point column into latitude, longitude
df_booking[['latitude', 'longitude', 'altitude']] = pd.DataFrame(df_booking['point'].tolist(), index=df_booking.index)
df_booking.head(1)

  0%|          | 10/6845 [00:08<1:50:20,  1.03it/s]RateLimiter caught an error, retrying (0/2 tries). Called with (*("hotel medici is set in a 19th-century building in milazzo's historic centre. it is 100 yards from the cathedral, 550 yards from the castle, and a 5-minute walk from the harbour for ferries to aelioan islands. rooms offer air conditioning and hydromassage showers.",), **{}).
Traceback (most recent call last):
  File "c:\Users\annas\anaconda3\envs\iron\lib\site-packages\geopy\extra\rate_limiter.py", line 136, in _retries_gen
    yield i  # Run the function.
  File "c:\Users\annas\anaconda3\envs\iron\lib\site-packages\geopy\extra\rate_limiter.py", line 274, in __call__
    res = self.func(*args, **kwargs)
  File "c:\Users\annas\anaconda3\envs\iron\lib\site-packages\geopy\geocoders\arcgis.py", line 173, in geocode
    return self._authenticated_call_geocoder(url, callback, timeout=timeout)
  File "c:\Users\annas\anaconda3\envs\iron\lib\site-packages\geopy\geocoders\arcgis.p

url              name  \
0  https://www.booking.com/hotel/it/b-amp-b-donna...  B&B Donna Teresa   

                                              pagina  \
0  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   

                                             address currentPrice  \
0  via giuseppe garibaldi, 137/b, 92100 , 92100 a...         € 76   

  previousPrice rating reviewNumber checkingDate  \
0         € 124    9.2  525 reviews   2023-09-03   

                                               image  ...  air_conditioning  \
0  https://cf.bstatic.com/xdata/images/hotel/squa...  ...  air conditioning   

           bathroom       wifi  breakfast  coffee_tea_maker  laundry  \
0  private bathroom  free wifi  breakfast  tea/coffee maker  laundry   

                                            location  \
0  (Via Giuseppe Garibaldi 137, 92100, Agrigento,...   

                                          point lon lat  
0  (37.31222999157022, 13.572039983036007, 0.0)          

[1 rows x 21 columns]

In [38]:
df_booking['latitude'].value_counts()

41.395600    34
36.872419    30
38.123020    26
38.123200    22
37.929855    19
             ..
37.768438     1
37.852672     1
37.157413     1
38.124980     1
37.885630     1
Name: latitude, Length: 1120, dtype: int64

In [35]:
df_booking['lon'] = df_booking.point.apply(lambda p: p.x)
df_booking['lat'] = df_booking.point.apply(lambda p: p.y)
df_booking.head(1)

AttributeError: 'tuple' object has no attribute 'x'

nulos: 3174, no nulos 3671

In [31]:
df_booking[df_booking['location'].isnull() == True]

url  \
9     https://www.booking.com/hotel/it/medici-milazz...   
29    https://www.booking.com/hotel/it/b-amp-b-sciar...   
34    https://www.booking.com/hotel/it/b-amp-b-palaz...   
44    https://www.booking.com/hotel/it/opera-boutiqu...   
46    https://www.booking.com/hotel/it/marla-39-s-bo...   
...                                                 ...   
7197  https://www.booking.com/hotel/it/b-amp-b-il-pa...   
7198  https://www.booking.com/hotel/it/maison-ortigi...   
7239  https://www.booking.com/hotel/it/b-amp-b-donna...   
7249  https://www.booking.com/hotel/it/zefiro-suites...   
7253  https://www.booking.com/hotel/it/il-giardino-d...   

                        name  \
9               Hotel Medici   
29        B&B Sciara Larmisi   
34      B&B Palazzo Perrotta   
44      Opera Boutique Rooms   
46    Marla's boutique rooms   
...                      ...   
7197          Maison Ortigia   
7198          Maison Ortigia   
7239   Saint cristofer house   
7249             Isole egadi   
7253              Casa do Re   

                                                 pagina  \
9     \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   
29    \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   
34    \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   
44    \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   
46    \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   
...                                                 ...   
7197  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   
7198  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   
7239  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   
7249  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   
7253  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   

                                                address currentPrice  \
9     hotel medici is set in a 19th-century building...        € 193   
29    offering a terrace and views of the garden, b&...         € 99   
34    set 350 yards from the centre of catania, 450 ...        € 127   
44    set in monreale, 350 yards from duomo di monre...         € 95   
46    the location was perfect, 200 meter walk from ...        € 100   
...                                                 ...          ...   
7197  located in siracusa in the sicily region, 200 ...        €  84   
7198  located in siracusa in the sicily region, 200 ...        €  84   
7239     at 600 mt.  from the ursino castle, 700 met...        €  73   
7249  situated 200 yards from the centre of trapani,...        €  80   
7253  casa do re features air-conditioned guest acco...       €  187   

     previousPrice rating   reviewNumber checkingDate  \
9              NaN    8.4    701 reviews   2023-09-03   
29             NaN    9.4  1,150 reviews   2023-09-03   
34             NaN    9.2    577 reviews   2023-09-03   
44             NaN    9.4    391 reviews   2023-09-03   
46             NaN    9.3    220 reviews   2023-09-03   
...            ...    ...            ...          ...   
7197         €  88    8.1  2,794 reviews   2023-09-04   
7198         €  88    8.1  2,794 reviews   2023-09-04   
7239         €  76    9.1     64 reviews   2023-09-04   
7249         €  84    9.0    278 reviews   2023-09-04   
7253        €  194    8.6     80 reviews   2023-09-04   

                                                  image  ...  \
9     https://cf.bstatic.com/xdata/images/hotel/squa...  ...   
29    https://cf.bstatic.com/xdata/images/hotel/squa...  ...   
34    https://cf.bstatic.com/xdata/images/hotel/squa...  ...   
44    https://cf.bstatic.com/xdata/images/hotel/squa...  ...   
46    https://cf.bstatic.com/xdata/images/hotel/squa...  ...   
...                                                 ...  ...   
7197  https://cf.bstatic.com/xdata/images/hotel/squa...  ...   
7198  https://cf.bstatic.com/xdata/images/hotel/squa...  ...   
7239  https://cf.bstatic.com/xdata/images/hotel/squa...  ...   
7249  https://cf.bstatic.com/xdata/images/hotel/squa...  ..

In [32]:
df_booking[df_booking['location'].isnull() == False]

url  \
0     https://www.booking.com/hotel/it/b-amp-b-donna...   
1     https://www.booking.com/hotel/it/alcantara-res...   
2     https://www.booking.com/hotel/it/giardini-sul-...   
3     https://www.booking.com/hotel/it/la-maison-del...   
4     https://www.booking.com/hotel/it/politeama-pal...   
...                                                 ...   
8087  https://www.booking.com/hotel/it/torre-don-vir...   
8102  https://www.booking.com/hotel/it/residence-gui...   
8112  https://www.booking.com/hotel/it/iblaresort.en...   
8120  https://www.booking.com/hotel/it/ossidiana.en-...   
8123  https://www.booking.com/hotel/it/casolare-nell...   

                                      name  \
0                         B&B Donna Teresa   
1               Alcantara Resort di Charme   
2     Giardini sul Mare - Mazara del Vallo   
3                       La Maison del Sole   
4                          Hotel Politeama   
...                                    ...   
8087      Torre Don Virgilio Country Hotel   
8102                   Residence Guidaloca   
8112             Iblaresort Boutique Hotel   
8120      Hotel Ossidiana Stromboli Center   
8123                 Casolare Nelle Saline   

                                                 pagina  \
0     \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   
1     \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   
2     \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   
3     \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   
4     \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   
...                                                 ...   
8087  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   
8102  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   
8112  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   
8120  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   
8123  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   

                                                address currentPrice  \
0     via giuseppe garibaldi, 137/b, 92100 , 92100 a...         € 76   
1     via colonnello francesco mannino, 98030 gaggi,...        € 162   
2     25 lungomare san vito, 91026 mazara del vallo,...         € 88   
3                   84 via napoli, 90133 palermo, italy         € 84   
4     piazza ruggiero settimo, 15, 90100 palermo, italy        € 131   
...                                                 ...          ...   
8087   via rocciola scrofani, 260, 97015 cannizzara,...       €  118   
8102  località guidaloca - scopello, 91014 scopello,...        €  88   
8112           via del mercato 105, 97100 ragusa, italy       €  152   
8120                 via marina, 98050 stromboli, italy       €  118   
8123    via murana 25 - nubia, 91027 torre nubia, italy        €  90   

     previousPrice rating   reviewNumber checkingDate  \
0            € 124    9.2    525 reviews   2023-09-03   
1              NaN    9.0    116 reviews   2023-09-03   
2              NaN    9.0    176 reviews   2023-09-03   
3              NaN    9.4  1,250 reviews   2023-09-03   
4              NaN    8.9  2,092 reviews   2023-09-03   
...            ...    ...            ...          ...   
8087        €  147    9.3    383 reviews   2023-09-06   
8102         €  97    8.3    624 reviews   2023-09-06   
8112        €  202    9.0    426 reviews   2023-09-06   
8120        €  134    8.5  1,354 reviews   2023-09-06   
8123        €  110    9.5    339 reviews   2023-09-06   

                                                  image  ...  \
0     https://cf.bstatic.com/xdata/images/hotel/squa...  ...   
1     https://cf.bstatic.com/xdata/images/hotel/squa...  ...   
2     https://cf.bstatic.com/xdata/images/hotel/squa...  ...   
3     https://cf.bstatic.com/xdata/images/hotel/squa...  ...   
4     https://cf.bstatic.com/xdata/images/hotel/squa...  ...   
...                                                 ...  ...   
8087  https://cf.bstatic.com/xdata/images/hotel/squa...  ...   
8102  https://cf.bs

In [39]:
map1 = folium.Map(
    location=[37.75120776952038, 14.992361985738308],
    tiles='cartodbpositron',
    zoom_start=12,
)
df_booking[df_booking['latitude'].isnull() == False].apply(lambda row:folium.CircleMarker(location=[row["latitude"], row["longitude"]]).add_to(map1), axis=1)
map1

In [40]:
df_booking.head(1)

url              name  \
0  https://www.booking.com/hotel/it/b-amp-b-donna...  B&B Donna Teresa   

                                              pagina  \
0  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   

                                             address currentPrice  \
0  via giuseppe garibaldi, 137/b, 92100 , 92100 a...         € 76   

  previousPrice rating reviewNumber checkingDate  \
0         € 124    9.2  525 reviews   2023-09-03   

                                               image  ...  breakfast  \
0  https://cf.bstatic.com/xdata/images/hotel/squa...  ...  breakfast   

   coffee_tea_maker  laundry  \
0  tea/coffee maker  laundry   

                                            location  \
0  (Via Giuseppe Garibaldi 137, 92100, Agrigento,...   

                                          point lon lat  latitude longitude  \
0  (37.31222999157022, 13.572039983036007, 0.0)          37.31223  13.57204   

  altitude  
0      0.0  

[1 rows x 24 columns]

revisa el formato de los precios, no está cogiendo bien los valores

In [42]:
df_booking['url_clean'] = df_booking['url'].str.split('?', expand=True)[0]
df_booking.head(1)

url              name  \
0  https://www.booking.com/hotel/it/b-amp-b-donna...  B&B Donna Teresa   

                                              pagina  \
0  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   

                                             address currentPrice  \
0  via giuseppe garibaldi, 137/b, 92100 , 92100 a...         € 76   

  previousPrice rating reviewNumber checkingDate  \
0         € 124    9.2  525 reviews   2023-09-03   

                                               image  ...  coffee_tea_maker  \
0  https://cf.bstatic.com/xdata/images/hotel/squa...  ...  tea/coffee maker   

   laundry                                           location  \
0  laundry  (Via Giuseppe Garibaldi 137, 92100, Agrigento,...   

                                          point lon lat  latitude longitude  \
0  (37.31222999157022, 13.572039983036007, 0.0)          37.31223  13.57204   

  altitude                                          url_clean  
0      0.0  https://www.booking.com/hotel/it/b-amp-b-donna...  

[1 rows x 25 columns]

In [45]:
os.getcwd()

'e:\\Cursos\\00ironhack_DA\\00LABS\\vuelve-conmigo-a-italia\\data\\pickle'

merge the new ones with the ones that are already geolocated

In [49]:
df_booking_done = pd.read_csv('../booking_merge.csv', sep='|')
df_booking_done.head(1)

url              name  \
0  https://www.booking.com/hotel/it/b-amp-b-donna...  B&B Donna Teresa   

                                              pagina  \
0  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   

                                             address currentPrice  \
0  via giuseppe garibaldi, 137/b, 92100 , 92100 a...         € 76   

  previousPrice  rating reviewNumber checkingDate  \
0         € 124     9.2  525 reviews   2023-09-03   

                                               image  ...  coffee_tea_maker  \
0  https://cf.bstatic.com/xdata/images/hotel/squa...  ...  tea/coffee maker   

   laundry                                      location  \
0  laundry  Via Giuseppe Garibaldi 137, 92100, Agrigento   

                                          point lon lat  latitude longitude  \
0  (37.31222999157022, 13.572039983036007, 0.0) NaN NaN  37.31223  13.57204   

  altitude                                          url_clean  
0      0.0  https://www.booking.com/hotel/it/b-amp-b-donna...  

[1 rows x 25 columns]

In [ ]:
df_total = pd.concat([df_booking, df_booking_done])
print(df_total.shape)
df_total.head(1)

clean values

In [71]:
df_total['currentPrice'] = df_total['currentPrice'].str.replace('€', '')
df_total['previousPrice'] = df_total['previousPrice'].str.replace('€', '')
df_total['reviewNumber'] = df_total['reviewNumber'].str.replace('reviews', '').str.replace('review', '')

In [78]:
df_total.head(1)

url              name  \
0  https://www.booking.com/hotel/it/b-amp-b-donna...  B&B Donna Teresa   

                                              pagina  \
0  \n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n\n...   

                                             address currentPrice  \
0  via giuseppe garibaldi, 137/b, 92100 , 92100 a...           76   

  previousPrice rating reviewNumber checkingDate  \
0           124    9.2         525    2023-09-03   

                                               image       parking  \
0  https://cf.bstatic.com/xdata/images/hotel/squa...  free parking   

   air_conditioning          bathroom       wifi  breakfast  coffee_tea_maker  \
0  air conditioning  private bathroom  free wifi  breakfast  tea/coffee maker   

   laundry                                           location  \
0  laundry  (Via Giuseppe Garibaldi 137, 92100, Agrigento,...   

                                          point lon lat  latitude  longitude  \
0  (37.31222999157022, 13.572039983036007, 0.0)          37.31223   13.57204   

   altitude                                          url_clean  
0       0.0  https://www.booking.com/hotel/it/b-amp-b-donna...

In [81]:
df_total['parking'] = np.where(df_total['parking'] == 'free parking', 'Y', 'N')
df_total['air_conditioning'] = np.where(df_total['air_conditioning'] == 'air conditioning', 'Y', 'N')
df_total['bathroom'] = np.where(df_total['bathroom'] == 'private bathroom', 'Y', 'N')
df_total['wifi'] = np.where(df_total['wifi'] == 'free wifi', 'Y', 'N')
df_total['breakfast'] = np.where(df_total['breakfast'] == 'breakfast', 'Y', 'N')
df_total['coffee_tea_maker'] = np.where(df_total['coffee_tea_maker'] == 'tea/coffee maker', 'Y', 'N')
df_total['laundry'] = np.where(df_total['laundry'] == 'laundry', 'Y', 'N')

export

In [82]:
df_total.drop(['pagina', 'url'], axis = 1).to_csv('../booking.csv', sep='|', encoding='utf-8', index = False)

In [47]:
with open(f'../booking.pickle', 'wb') as data_scrapeado:
    pickle.dump(df_total, data_scrapeado)